# 3. C programming

The following code is needed only if you are using the notebook, because <tt>make</tt> command treats spaces and TAB characters differently.  We need to be able to reconfigure Jupyter to treat TABS as characters, not replace them with 4 spaces, as it does by default.

In [ ]:
%%javascript
IPython.tab_as_tab_everywhere = function(use_tabs) {
    if (use_tabs === undefined) {
        use_tabs = true; 
        }
    // apply setting to all current CodeMirror instances
    IPython.notebook.get_cells().map(
        function(c) {  return c.code_mirror.options.indentWithTabs=use_tabs;  }
        );
    // make sure new CodeMirror instances created in the future also use this setting
    CodeMirror.defaults.indentWithTabs=use_tabs;
    };

IPython.tab_as_tab_everywhere()

## Gaussian packet evolution: a C project

This is the first homework to be handed in, a week-long project to graphically illustrate what happens to a Gaussian wave packet (we will make it up by adding a few individual waves) impacting on a barrier. We want to observe how some of the packet is reflected, and some undergoes quantum-mechanical tunneling, so both a reflected and a transmitted packet emerges after the impact.  We will run the program repeatedly, changing the number of wave making up the packet, the number of points to plot, the initial energy of the incoming packet, etc. The physics of this scattering process will get discussed next, but first let's set up the mechanics of the new project:
<ul>
	<li>make a project subdirectory
	<li>create a basic skeleton of a program that can read and parse user input (though does not compute anything at first)
	<li>have a basic Makefile in place
</ul>
<p>
The second part of the homework is to try to figure out what is going on in an old Fortran program that does the same thing. We do not know either Fortran or C syntax, but hopefully the computational content, i.e. the algorithmic core, will be self-explanatory. The task is to "port", or convert this old code to C, and learn some basic C programming in the process.

In [ ]:
%%bash
## start with an empty directory for the project
if [ ! -d ~/5P10 ]; then
  mkdir ~/5P10
fi
cd ~/5P10
rm -rf packet
mkdir packet

In [ ]:
%cd ~/5P10/packet

In [ ]:
%%bash
pwd
ls -l

## Physics of tunnelling

Review <a href="https://www.physics.brocku.ca/Courses/5P10/Lectures/wavepackets.pdf" target="_blank">these notes from a QM course (PDF)</a>.

Last session, we saw a working Fortran program. The relevant numerical part is this, and the notation is a straightforward translation of the expressions from the PDF notes.  FORTRAN = "FORmula TRANslation".

In [ ]:
%%file add_wave.f
C=======================================================================	
	subroutine add_wave(x,P,A,E)
C..adds the specified wave to the the supplied complex storage array P
C  the values of Psi are only calculated at points given in real array x 
	real*4 		x(601),E
	complex*8	P(601),I,A,k1,K2,C1,b,c,d,f

	I = cmplx(0.,1.)	!complex i

	k1 = sqrt(cmplx(E,0.))
	K2 = sqrt(cmplx(E-1.,0.))

	C1 = -2*k1*K2-k1**2-2*k1*K2*exp(4*I*K2)+exp(4*I*K2)*k1**2
     *	-K2**2+K2**2*exp(4*I*K2)

	b = (k1**2-K2**2)/ C1 *(exp(2*I*(2*K2-k1))-exp(-2*I*k1))
	c = -2*k1*(K2+k1)/ C1 *exp(I*(K2-k1))
	d = (-2*K2+2*k1)*k1/ C1 *exp(I*(-k1+3*K2))
	f = -4*k1*K2/ C1 *exp(2*I*(K2-k1))

	do j = 1,296		! left of the barrier, x < -1
	  P(j) = P(j) + A * ( exp(I*k1*x(j)) + b*exp(-I*k1*x(j)) )
	end do
	do j=297,304		! inside the barrier, -1 < x < 1
	  P(j) = P(j) + A * ( c*exp(I*K2*x(j)) + d*exp(-I*K2*x(j)) )
	end do
	do j=305,601		! to the right of the barrier, x > 1
	  P(j) = P(j) + A * f*exp(I*k1*x(j))
	end do
	  
 	return
	end

## The beginnings of a C program

Now we are ready to dive into C. We'll start with a simple skeleton C program, slightly enhanced compared to the version discussed the last time. The numeric heart of the program is still missing, and the output consists of meaningless numbers.

We will need a Makefile and a gnuplot kernel loaded, for inline graphs.

In [ ]:
%%file Makefile

OBJ = packet.o

# these are pre-defined, but we can also change the default behaviour, if we have multiple compilers
CC = cc
#CC = icc
CFLAGS = -O -DVERSION="\"`date '+%Y-%b-%d-%H:%M'`\"" 
LIBS = -lm

# special abbreviations: $@ is the file to be made; $? is the changed dependent(s).

packet: $(OBJ)
	$(CC) $(CFLAGS) -o $@ $(OBJ) $(LIBS)

# this is the default implicit rule to convert xxx.c into xxx.o 
.c.o:
	$(CC) $(CFLAGS) -c $<

clean:
	rm -f packet *.o *~ core

In [ ]:
%%file Vo.dat
-75	0
-1	0
-1	1
1	1
1	0
75	0

In [ ]:
%load_ext gnuplot_kernel

In [ ]:
%gnuplot inline pngcairo font "Arial,16" size 800,600

In [ ]:
%%file packet.c
/*
 * packet.c
 *   packet - generate a Gaussian wavepacket impacting on an energy barrier.
 *
 * Completed: January.2018 (c) E.Sternin
 * Revisions: 
 *
 */

#ifndef VERSION           /* date-derived in Makefile */
#define VERSION "2018.01" /* default, that's when we first wrote the program */
#endif

#include <stdarg.h>
#include <stdio.h>
#include <stdlib.h>
#include <string.h>
#include <ctype.h>
#include <unistd.h>
#include <sys/types.h>
#include <sys/stat.h>
#include <fcntl.h>
#include <math.h>
#include <complex.h>

#define MAX_STR 256
#define NPTS    601       /* these cannot be changed via command-line switches */
#define X_MIN   -75.0
#define X_MAX    75.0
#define NS        4       /* +/- NS * sigma is the extent of the Gaussian packet we calculate */

/* Global variables */

static char whoami[MAX_STR] ;        /* argv[0] will end up here */
static int  verbosity;               /* Show detailed information */
static char options[] = "Vvhn:t:U:p:s:x:";   /* command-line options, : means takes a value */
static char help_msg[] = "\
%s [<options>]\n\
\t-V        report version information\n\
\t-v        increase verbosity, may combine several\n\
\t-n #      number of waves making up the packet\n\
\t-t #      time since the beginning\n\
\t-U #      U[=16] height of the barrier U(x), in epsilon\n\
\t-p #      p0[=0.5] is the mean momentum of the packet\n\
\t-s #      s[=0.1] is the width of the packet in p-space\n\
\t-x #      x0[=-25] is the initial position of the packet\n\
\t-h        help message\n\
\n\
e.g.\tpacket -v -n 20 -t 20 -p 0.5 -s 0.1\n" 
;

/*************************************************service routines************/

void __attribute__((noreturn)) die(char *msg, ...) {
  va_list args;
  va_start(args, msg);
  vfprintf(stderr, msg, args);
  fputc('\n', stderr);
  exit(1);
  }

/************************************************************** main *********/
int main(int argc, char **argv) {
  int    i,j,n;
  double t,U,p0,s,x0,dx,x[NPTS],A0,p_step,p_now,E;
  double complex Psi[NPTS];

  double Pi = 2.*acos(0.);

/*
 *  default values, may get changed by the command-line options
 */
  verbosity = 0;    /* 0 = quiet by default, 1 = info, 2 = debug */	
  n = 20;           /* default to 41=(2*n+1) waves in the packet */
  p0 = 0.5;         /* default to 0.5 in p-space */
  s = 0.1;          /* keep to less than 1/4 of p0, so that (p0+/-4s) > 0, all */
                    /* constituent waves travel to the right initially */
  U = 1;            /* barrier height, in epsilon */
  x0 = -25;         /* initial position of the packet */
  t = 0;

  strncpy(whoami, argv[0], MAX_STR);

  while ((i = getopt(argc, argv, options)) != -1)
    switch (i) {
      case 'V':
         printf(" %s: version %s\n",whoami,VERSION);
         break;
      case 'v':
         verbosity++;
         if (verbosity > 1) printf(" %s: verbosity level set to %d\n",whoami,verbosity);
         break;
      case 'h':
         die(help_msg,whoami);
         break;
      case 'n':
         if ( ((n = atoi(optarg)) > 10000) || n < 10 )
           die(" %s: -n %d is not a valid number of points (10..10000)\n",whoami,n);
         if (verbosity > 1) printf(" %s: Number of points = %d\n",whoami,n);
         break;
      case 't':
         if ( ((t = atof(optarg)) < 0) )
           die(" %s: -t %d is not a valid time\n",whoami,t);
         if (verbosity > 1) printf(" %s: time = %f\n",whoami,t);
         break;
      case 'U':
         U = atof(optarg);
         if (verbosity > 1) printf(" %s: barrier height is = %f epsilon\n",whoami,U);
         break;
      case 'p':
         p0 = atof(optarg);
         if (verbosity > 1) printf(" %s: mean momentum of packet is p0 = %f\n",whoami,p0);
         break;
      case 's':
         if ( (s = atof(optarg)) < 1e-2 )
           die(" %s: -s %f is not a valid packet width, >= 1e-2\n",whoami,s);
         if (verbosity > 1) printf(" %s: width of packet, s = %f\n",whoami,s);
         break;
      case 'x':
         if ( ((x0 = atof(optarg)) < X_MIN) || x0 > 0)
           die(" %s: -x %f is not a valid packet position, %d..0\n",whoami,x0,X_MIN);
         if (verbosity > 1) printf(" %s: initial position of packet, x0 = %f\n",whoami,x0);
         break;
      default:
         if (verbosity > 0) die(" try %s -h\n",whoami);	/* otherwise, die quietly */
         return 0;
      }

/*
 * when we get here, we parsed all user input, and are ready to calculate things
 */

  if ((p0-NS*s) <= 0) /* is the smallest value of p still positive ? */
     die(" %s: some waves in the packet p=%f+/-%d*%f are not travelling to the right at t=0\n",whoami,p0,NS,s);

  if ((p0+NS*s) >= sqrt(U)) /* is the largest value of p still below U of the barrier ? */
     die(" %s: some waves in the packet p=%f+/-%d*%f have energy >= U=%f\n",whoami,p0,NS,s,U);

  dx = (X_MAX-X_MIN)/(double)(NPTS-1);
  for (j=0; j < NPTS; j++) { 
     x[j]=X_MIN + j*dx;
     Psi[j] = (double complex)0.0;  /* start with a blank Psi(x) */
     }


  /*
   * here we compute Psi(x,t), blank for now
   */


  /* output the total Psi as is, without normalization */
  for (j=0; j < NPTS; j++) {
     if (verbosity > 0) printf("\t%f\t%f\t%f\t%f\n",x[j],cabs(Psi[j]),creal(Psi[j]),cimag(Psi[j]));
     }

  return 0;
  }

In [ ]:
%%bash
make
./packet -v

We can even test the gnuplot script, but of course for all t values, the output is zero everywhere.

In [ ]:
%%gnuplot
set style data line
set yrange [-0.1:1.1]
set xrange [-60:60]
set xlabel "x/a"
set ylabel "Psi^2"
set title "Scattering of a Gaussian wave packet (41 waves), E=V/4"
plot \
  'Vo.dat' t "V(x)",\
  '<./packet -v -t 0' title "t=0",\
  '<./packet -v -t 20' title "t=20",\
  '<./packet -v -t 50' title "t=50"

## Notes on Fortran-to-C conversion

Fortran:
<pre>
    real*4      x(601), ...
	complex*8   P(601), ...
	...
	do j = 1,601
	  x(j) = -75 + (j-1)*0.25
	  P(j) = cmplx(0.,0.)
	end do
</pre>

C:
<pre>
...
#include &lt;math.h&gt;
#include &lt;complex.h&gt;

#define NPTS    601       /* these cannot be changed via command-line switches */
#define X_MIN   -75.0
#define X_MAX    75.0
...
  double dx,x[NPTS], ...;
  double complex Psi[NPTS];
...
  dx = (X_MAX-X_MIN)/(double)(NPTS-1);
  for (j=0; j < NPTS; j++) { 
     x[j]=X_MIN + j*dx;
     Psi[j] = (double complex)0.0;  /* start with a blank Psi(x) */
     }
</pre>

Fortran:
<pre>
	I = cmplx(0.,1.)	!complex i

	k1 = sqrt(cmplx(E,0.))
	K2 = sqrt(cmplx(E-1.,0.))

	C1 = -2*k1*K2-k1**2-2*k1*K2*exp(4*I*K2)+exp(4*I*K2)*k1**2
     *	-K2**2+K2**2*exp(4*I*K2)

	b = (k1**2-K2**2)/ C1 *(exp(2*I*(2*K2-k1))-exp(-2*I*k1))
	c = -2*k1*(K2+k1)/ C1 *exp(I*(K2-k1))
	d = (-2*K2+2*k1)*k1/ C1 *exp(I*(-k1+3*K2))
	f = -4*k1*K2/ C1 *exp(2*I*(K2-k1))
</pre>

C:
<pre>
#include &lt;complex.h&gt;
...
  for (i=-n; i < n; i++) {
    p_now = p0 + (double)i * p_step;
    E = p_now*p_now;
    A = A0*exp(-pow((p_now-p0)/(2*s),2))*cexp(-I*(p_now*x0 + E*t));

    k1 = csqrt((double complex)(E));
    k2 = csqrt((double complex)(E-U));
    ce4 = cexp(4*I*k2);
    C1 = -2*k1*k2-k1*k1-2*k1*k2*ce4+ce4*(k1*k1+k2*k2)-k2*k2;

    b = (k1*k1-k2*k2)/ C1 *(cexp(2*I*(2*k2-k1))-cexp(-2*I*k1));
    c = -2*k1*(k2+k1)/ C1 *cexp(I*(k2-k1));
    d = (-2*k2+2*k1)*k1/ C1 *cexp(I*(-k1+3*k2));
    f = -4*k1*k2/ C1 *cexp(2*I*(k2-k1));

    ...
  }
</pre>

Fortran:
<pre>
	do j = 1,296		! left of the barrier, x < -1
	  P(j) = P(j) + A * ( exp(I*k1*x(j)) + b*exp(-I*k1*x(j)) )
	end do
	do j=297,304		! inside the barrier, -1 < x < 1
	  P(j) = P(j) + A * ( c*exp(I*K2*x(j)) + d*exp(-I*K2*x(j)) )
	end do
	do j=305,601		! to the right of the barrier, x > 1
	  P(j) = P(j) + A * f*exp(I*k1*x(j))
	end do
</pre>

C:
<pre>
    for (j=0; j < NPTS; j++) {
       if (x[j] < -1.) {         /* to the left of the barrier, x < -1 */
          Psi[j] += A*( cexp(I*k1*x[j]) + b*cexp(-I*k1*x[j]) );
          }
       else if (x[j] > 1.) {     /* to the right of the barrier, x > 1 */
          Psi[j] += A*f*cexp(I*k1*x[j]);
          }
       else {                    /* inside the barrier, -1 < x < 1 */
          Psi[j] += A*( c*cexp(I*k2*x[j]) + d*cexp(-I*k2*x[j]) );
          }
       }
</pre>